In [1]:
# This is necessary to recognize the modules
import os
import sys
from decimal import Decimal

import pandas as pd

root_path = os.path.abspath(os.path.join(os.getcwd(), '../..'))
sys.path.append(root_path)

In [2]:
def load_market_data(connector_name: str, trading_pair: str, data_type: str = "order_book") -> pd.DataFrame:
    """
    Load market data from files for a specific connector and trading pair.
    
    Args:
        connector_name: Name of the connector (e.g., "bitmart_paper_trade")
        trading_pair: Trading pair symbol (e.g., "LINK-USDT")
        data_type: Type of data to load ("order_book" or "trades")
    
    Returns:
        pd.DataFrame: Concatenated DataFrame containing all data from matching files
    """
    folder = root_path + f"/data/order_book/"
    
    # Define the pattern based on data type
    pattern = "order_book_snapshots" if data_type == "order_book" else "trades"
    
    # Find all matching files
    files = [
        file for file in os.listdir(folder) 
        if connector_name in file 
        and trading_pair in file 
        and pattern in file
    ]
    
    if not files:
        raise FileNotFoundError(f"No {data_type} files found for {connector_name} {trading_pair}")
    
    # Load and concatenate all matching files
    dfs = []
    for file in files:
        df = pd.read_json(folder + "/" + file, lines=True)
        dfs.append(df)
    
    return pd.concat(dfs, ignore_index=True)

# Example usage:
order_book_df = load_market_data("bitmart_paper_trade", "LINK-USDT", "order_book")
trades_df = load_market_data("bitmart_paper_trade", "LINK-USDT", "trades")


In [3]:
order_book_df

ts                                               bids  \
0      1732896371  [[18.0799, 4.22], [18.0707, 1.04], [18.0706, 7...   
1      1732896372  [[18.0707, 1.04], [18.0706, 7.29], [18.0697, 5...   
2      1732896373  [[18.0707, 1.04], [18.0706, 7.29], [18.0697, 5...   
3      1732896374  [[18.0707, 1.04], [18.0706, 7.29], [18.0697, 5...   
4      1732896375  [[18.0708, 1.47], [18.0707, 1.04], [18.0706, 7...   
...           ...                                                ...   
19350  1732917134  [[18.1118, 2.5], [18.0906, 1.03], [18.0905, 8....   
19351  1732917135  [[18.1118, 2.5], [18.0906, 1.03], [18.0905, 8....   
19352  1732917136  [[18.1118, 2.5], [18.0906, 1.03], [18.0905, 8....   
19353  1732917137  [[18.1118, 2.5], [18.0906, 1.03], [18.0905, 8....   
19354  1732917138  [[18.1118, 2.5], [18.0906, 1.03], [18.0905, 8....   

                                                    asks  
0      [[18.1645, 3.6], [18.1646, 6.1], [18.1794, 5.9...  
1      [[18.1643, 3.6], [18.1644, 6.1], [18.1646, 8.9...  
2      [[18.1643, 3.6], [18.1644, 6.1], [18.1646, 8.9...  
3      [[18.1641, 3.6], [18.1642, 15.08], [18.1794, 8...  
4      [[18.164, 6.1], [18.1641, 3.6], [18.1642, 8.98...  
...                                                  ...  
19350  [[18.1998, 6.1], [18.1999, 3.6], [18.2001, 8.9...  
19351  [[18.1998, 6.1], [18.1999, 3.6], [18.2001, 8.9...  
19352  [[18.1998, 6.1], [18.1999, 3.6], [18.2001, 8.9...  
19353  [[18.1998, 6.1], [18.1999, 3.6], [18.2001, 8.9...  
19354  [[18.1998, 6.1], [18.1999, 3.6], [18.2001, 8.9...  

[19355 rows x 3 columns]

In [4]:
exchanges = ["bitmart_paper_trade", "ascend_ex_paper_trade"]
trading_pair = "LINK-USDT"

# get all the order book files and trades files
# unpack the best bid and best ask for the columns bids and asks of the dataframe (is the first observation of the list that is a tuple (amount, price))
# plot with scatter the best bid and best ask over time
# plot with scatter the trades over time
# plot with scatter the mid price over time
# plot with scatter the bid ask spread over time

ob_data = {}
trades_data = {}

for exchange in exchanges:
    # Load the order book data
    ob = load_market_data(exchange, trading_pair, "order_book")
    ob["best_bid_price"] = ob["bids"].apply(lambda x: x[0][0])
    ob["best_ask_price"] = ob["asks"].apply(lambda x: x[0][0])
    ob["best_bid_amount"] = ob["bids"].apply(lambda x: x[0][1])
    ob["best_ask_amount"] = ob["asks"].apply(lambda x: x[0][1])
    ob.index = pd.to_datetime(ob["ts"], unit="s")
    ob_data[exchange] = ob
    # Load the trades data
    trades = load_market_data(exchange, trading_pair, "trades")
    trades["amount_quote"] = trades["q_base"] * trades["price"]
    trades.index = pd.to_datetime(trades["ts"], unit="s")
    trades_data[exchange] = trades


In [5]:
trades_data["bitmart_paper_trade"]

ts    price  q_base  side  amount_quote
ts                                                                  
2024-11-29 16:06:20  1732896380  18.1200    0.56   buy     10.147200
2024-11-29 16:06:39  1732896399  18.0902    0.47   buy      8.502394
2024-11-29 16:06:41  1732896401  18.0901    0.45  sell      8.140545
2024-11-29 16:06:43  1732896403  18.0900    0.47  sell      8.502300
2024-11-29 16:06:45  1732896405  18.0899    0.38  sell      6.874162
...                         ...      ...     ...   ...           ...
2024-11-29 21:45:57  1732916757  18.0999    0.82  sell     14.841918
2024-11-29 21:46:07  1732916767  18.0999    0.37   buy      6.696963
2024-11-29 21:46:09  1732916769  18.1102    0.38  sell      6.881876
2024-11-29 21:46:21  1732916781  18.1103    0.45   buy      8.149635
2024-11-29 21:46:27  1732916787  18.1201    0.38   buy      6.885638

[4103 rows x 5 columns]

In [6]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def plot_market_data(ob_df: pd.DataFrame, trades_df: pd.DataFrame, exchange: str, levels_to_plot: int = 10):
    """
    Create a plotly figure with order book and trades data.
    """
    fig = go.Figure()
    for level in range(1, levels_to_plot + 1):
        bids_price = ob_df["bids"].apply(lambda x: x[level][0])
        bids_amount = ob_df["bids"].apply(lambda x: x[level][1])
        asks_price = ob_df["asks"].apply(lambda x: x[level][0])
        asks_amount = ob_df["asks"].apply(lambda x: x[level][1])
        
        # Plot the bid line and add with color intensity based on amount

        fig.add_trace(
            go.Scatter(
                x=ob_df.index,
                y=bids_price,
                mode='lines',
                name=f'Bid {level}',
                line=dict(width=1),
                marker=dict(
                    size=6,
                    color=bids_amount,
                    colorscale='Reds',
                    showscale=True,
                    colorbar=dict(title='Bid Amount')
                )
            )
        )
        fig.add_trace(
            go.Scatter(
                x=ob_df.index,
                y=asks_price,
                mode='lines',
                name=f'Ask {level}',
                line=dict(width=1),
                marker=dict(
                    size=6,
                    color=asks_amount,
                    colorscale='Reds',
                    showscale=True,
                    colorbar=dict(title='Ask Amount')
                )
            )
        )

    
    # Trades trace remains unchanged
    fig.add_trace(
        go.Scatter(
            x=trades_df.index,
            y=trades_df['price'],
            mode='markers',
            name='Trades',
            marker=dict(
                # size=trades_df['amount_quote'] * 2,
                symbol='circle',
                color='blue',
                opacity=0.5
            )
        )
    )
    
    # Update layout
    fig.update_layout(
        title=f'Market Data for {exchange}',
        xaxis_title='Timestamp',
        yaxis_title='Price',
        showlegend=True
    )
    
    return fig
# Create plots for each exchange
for exchange in exchanges:
    fig = plot_market_data(
        ob_df=ob_data[exchange],
        trades_df=trades_data[exchange],
        exchange=exchange,
        levels_to_plot=1
    )
    fig.show()